# TRAINING I3W


# A) Create Envorinment, Vehicles etc

### General Parameter

In [1]:
# Define horizon as a variable to ensure consistent use across notebook (length of one rollout)
HORIZON=500

# name of the experiment
experiment_name = "IntersectionExample"

# scenario class
import flow.scenarios as scenarios
print("Available scenarios:")
print(scenarios.__all__)
scenario_name = "IntersectionTWScenario"

# environment class
import flow.multiagent_envs as flowenvs
print("\nAvailable environments:")
print(flowenvs.__all__)
env_name = "MultiAgentIntersectionEnv"

Available scenarios:
['Scenario', 'BayBridgeScenario', 'BayBridgeTollScenario', 'BottleneckScenario', 'Figure8Scenario', 'SimpleGridScenario', 'HighwayScenario', 'LoopScenario', 'MergeScenario', 'TwoLoopsOneMergingScenario', 'MultiLoopScenario', 'IntersectionScenarioTW']

Available environments:
['MultiEnv', 'MultiAgentAccelEnv', 'MultiWaveAttenuationPOEnv', 'MultiAgentIntersectionEnv', 'MultiAgentTeamSpiritIntersectionEnv']


### Net Parameter

In [2]:
from flow.core.params import NetParams
from flow.scenarios.intersection import ADDITIONAL_NET_PARAMS

additionalNetParams = {
            "edge_length": 40,
            "lanes": 1,
            "speed_limit": 30
        }

net_params = NetParams( no_internal_links=False,                  #default: True   !! damit Kreuzungen nicht überspr. werden
                        inflows=None,                             #default: None
                        osm_path=None,                            #default: None
                        netfile=None,                             #default: None
                        additional_params=additionalNetParams     #default: None   !!
                      )

### InitialConfig Parameter

In [3]:
from flow.core.params import InitialConfig

initial_config = InitialConfig( shuffle=True,                            #default: False         !!
                                spacing="custom",                        #default: "uniform"     !!
                                min_gap=10,                              #default: 0
                                perturbation=29.99,                      #default: 0.0            !!        
                                x0=0,                                    #default: 0
                                bunching=0,                              #default: 0
                                lanes_distribution=float("inf"),         #default: float("inf")
                                edges_distribution="all",                #default: "all"
                                additional_params=None )                 #default: None

### SUMO Parameter

In [4]:
from flow.core.params import SumoParams

sumo_params = SumoParams( port = None,                  #default: None
                          sim_step=0.1,                 #default: 0.1
                          emission_path=None,           #default: None
                          lateral_resolution=None,      #default: None
                          no_step_log=True,             #default: True
                          render=False,                 #default: False
                          save_render=False,            #default: False
                          sight_radius=25,              #default: 25
                          show_radius=False,            #default: False
                          pxpm=2,                       #default: 2
                          overtake_right=False,         #default: False    
                          seed=None,                    #default: None
                          restart_instance=False,       #default: False
                          print_warnings=True,          #default: True
                          teleport_time=-1,             #default: -1
                          num_clients=1,                #default: 1
                          sumo_binary=None )            #default: None

### Environment Parameter

In [5]:
from flow.core.params import EnvParams

additionalEnvParams = {
        # maximum acceleration of autonomous vehicles
        "max_accel": 3,
        # maximum deceleration of autonomous vehicles
        "max_decel": 3,
        "target_velocity": 30
    }

env_params = EnvParams( additional_params=additionalEnvParams, #default: None    !!
                        horizon=HORIZON,                       #default: 500     !!
                        warmup_steps=0,                        #default: 0       
                        sims_per_step=1,                       #default: 1
                        evaluate=False )                       #default: False

### Vehicles Parameter

In [6]:
from flow.core.params import VehicleParams

# import vehicles dynamics models
#from flow.controllers import SumoCarFollowingController
from flow.controllers import ContinuousRouter
#from flow.controllers.lane_change_controllers import SumoLaneChangeController
from flow.controllers.lane_change_controllers import StaticLaneChanger
from flow.controllers import RLController
from flow.core.params import SumoLaneChangeParams
from flow.core.params import SumoCarFollowingParams
from random import *

vehicles = VehicleParams()

#### Add RL-Agent controlled vehicles 

In [7]:
# car following parameters, default: None
cf_parameter = SumoCarFollowingParams(
                speed_mode="aggressive")
# lane change parameters, default: None
lc_parameter =  None

vehicles.add( # name of the vehicle
                veh_id = "rl",
              # acceleration controller, default: (SumoCarFollowingController, {})
                acceleration_controller=(RLController, {}),
              # lane_change_controller, default: (SumoLaneChangeController, {})
                lane_change_controller=(StaticLaneChanger,{}),
              # routing controller, default: None
                routing_controller=(ContinuousRouter, {}),
              # initial speed, default: 0
                initial_speed=0,
              # number of vehicles, default: 1 
                num_vehicles=2,
                
                car_following_params=cf_parameter
              # speed mode, default: "right_of_way"
                #speed_mode="aggressive",
              # lane change mode, default: "no_lat_collide"
                #lane_change_mode="aggressive", 
              # car following parameter, default: None
                #sumo_car_following_params=cf_parameter,
              # lane change parameter, default: None
                #sumo_lc_params=lc_parameter
)

### Flow Parameter

In [8]:
# Creating flow_params. Make sure the dictionary keys are as specified. 
flow_params = dict( # name of the experiment
                      exp_tag=experiment_name,
                    # name of the flow environment the experiment is running on
                      env_name=env_name,
                    # name of the scenario class the experiment uses
                      scenario=scenario_name,
                    # simulator that is used by the experiment
                      simulator='traci',
                    # sumo-related parameters (see flow.core.params.SumoParams)
                      sim=sumo_params,
                    # environment related parameters (see flow.core.params.EnvParams)
                      env=env_params,
                    # network-related parameters (see flow.core.params.NetParams and
                    # the scenario's documentation or ADDITIONAL_NET_PARAMS component)
                      net=net_params,
                    # vehicles to be placed in the network at the start of a rollout 
                    # (see flow.core.vehicles.Vehicles)
                      veh=vehicles,
                   # (optional) parameters affecting the positioning of vehicles upon 
                   # initialization/reset (see flow.core.params.InitialConfig)
                      initial=initial_config
                )

# B) Training

In [9]:
import json

import ray
try:
    from ray.rllib.agents.agent import get_agent_class
except ImportError:
    from ray.rllib.agents.registry import get_agent_class
from ray.tune import run_experiments
from ray.tune.registry import register_env

from flow.utils.registry import make_create_env
from flow.utils.rllib import FlowParamsEncoder

from ray import tune
from ray.rllib.agents.ppo.ppo_policy_graph import PPOPolicyGraph

In [10]:
# number of parallel workers
N_CPUS = 2
# number of rollouts per training iteration
N_ROLLOUTS = 20

ray.init(redirect_output=True, num_cpus=N_CPUS+1)

Process STDOUT and STDERR is being redirected to /tmp/ray/session_2019-03-12_18-24-26_26953/logs.
Waiting for redis server at 127.0.0.1:43529 to respond...
Waiting for redis server at 127.0.0.1:34858 to respond...
Starting the Plasma object store with 6.554658406 GB memory using /dev/shm.

View the web UI at http://localhost:8890/notebooks/ray_ui.ipynb?token=1667cf0b8490b75b968f56a120accd5075d84837f2ed6c11



{'node_ip_address': '192.168.2.102',
 'object_store_addresses': ['/tmp/ray/session_2019-03-12_18-24-26_26953/sockets/plasma_store'],
 'raylet_socket_names': ['/tmp/ray/session_2019-03-12_18-24-26_26953/sockets/raylet'],
 'redis_address': '192.168.2.102:43529',
 'webui_url': 'http://localhost:8890/notebooks/ray_ui.ipynb?token=1667cf0b8490b75b968f56a120accd5075d84837f2ed6c11'}

In [11]:
def executeTraining():
    
    # The algorithm or model to train. This may refer to "
    #      "the name of a built-on algorithm (e.g. RLLib's DQN "
    #      "or PPO), or a user-defined trainable function or "
    #      "class registered in the tune registry.")
    alg_run = "PPO"

    agent_cls = get_agent_class(alg_run)
    config = agent_cls._default_config.copy()
    config["num_workers"] = N_CPUS  # number of parallel workers
    config["train_batch_size"] = HORIZON * N_ROLLOUTS  # batch size
    config["gamma"] = 0.999  # discount rate
    config["model"].update({"fcnet_hiddens": [64, 32]})  # size of hidden layers in network
    config["use_gae"] = True  # using generalized advantage estimation
    config["lambda"] = 0.97  
    #config["sgd_minibatch_size"] = min(16 * 1024, config["train_batch_size"])  # stochastic gradient descent
    #config["sample_batch_size"] = config["train_batch_size"]/config["num_workers"] # 200 default, trotzdem zu hoch?
    config["kl_target"] = 0.02  # target KL divergence
    config["num_sgd_iter"] = 10  # number of SGD iterations
    config["horizon"] = HORIZON  # rollout horizon

    # save the flow params for replay
    flow_json = json.dumps(flow_params, cls=FlowParamsEncoder, sort_keys=True,
                           indent=4)  # generating a string version of flow_params
    config['env_config']['flow_params'] = flow_json  # adding the flow_params to config dict
    config['env_config']['run'] = alg_run

    # Call the utility function make_create_env to be able to 
    # register the Flow env for this experiment
    create_env, gym_name = make_create_env(params=flow_params, version=0)

    # Register as rllib env with Gym
    register_env(gym_name, create_env)
    
    # multi agent policy mapping
    test_env = create_env()
    obs_space = test_env.observation_space
    act_space = test_env.action_space

    def gen_policy():
        return (PPOPolicyGraph, obs_space, act_space, {})

    # Setup PG with an ensemble of `num_policies` different policy graphs
    policy_graphs = {'rl_0': gen_policy(), 'rl_1': gen_policy()}
    
    def policy_mapping_fn(agent_id):
        return agent_id

    config.update({
            'multiagent': {
                'policy_graphs': policy_graphs,
                'policy_mapping_fn': tune.function(policy_mapping_fn)
            }
        })
    
    trials = run_experiments({
        flow_params["exp_tag"]: {
            "run": alg_run,  # RL algorithm to run
            "env": gym_name,  # environment name generated earlier
            "config": {  # configuration params (must match "run" value)
                **config
            },
            "checkpoint_freq": 1,  # number of iterations between checkpoints
            "max_failures": 999,
            "stop": {  # stopping conditions
                "training_iteration": 300,  # number of iterations to stop after
            },
        },
    })

In [12]:
executeTraining()

 Starting SUMO on port 51275
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.8/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-12_18-24-28tsnpscrn -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



24.311956666327163
25.838955093458935


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_18-25-24
  done: false
  episode_len_mean: 455.04761904761904
  episode_reward_max: 270.75795500964466
  episode_reward_mean: 47.97779331562042
  episode_reward_min: -168.11321703014733
  episodes_this_iter: 21
  episodes_total: 21
  experiment_id: 3c083513fdcf4257a3e2216ed5864a2f
  hostname: Gandalf
  info:
    grad_time_ms: 4580.163
    load_time_ms: 146.605
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4170949459075928
      kl: 0.0007874090224504471
      policy_loss: -0.0008958953549154103
      total_loss: 113.08045196533203
      vf_explained_var: 0.0426790677011013
      vf_loss: 113.0811767578125
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4219223260879517
      kl: 0.0008876294014044106
      policy_loss: -0.00087617355

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=26994], 123 s, 5 iter, 50000 ts, 112 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_18-27-26
  done: false
  episode_len_mean: 428.62
  episode_reward_max: 372.9499641757883
  episode_reward_mean: 153.71626407892748
  episode_reward_min: -163.1948929522456
  episodes_this_iter: 26
  episodes_total: 137
  experiment_id: 3c083513fdcf4257a3e2216ed5864a2f
  hostname: Gandalf
  info:
    grad_time_ms: 3735.603
    load_time_ms: 26.618
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.39472234249115
      kl: 0.009146330878138542
      policy_loss: -0.004239782225340605
      total_loss

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=26994], 245 s, 10 iter, 100000 ts, 230 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_18-29-29
  done: false
  episode_len_mean: 228.34
  episode_reward_max: 364.5445274538058
  episode_reward_mean: 222.60110423242813
  episode_reward_min: -157.92623549375963
  episodes_this_iter: 47
  episodes_total: 332
  experiment_id: 3c083513fdcf4257a3e2216ed5864a2f
  hostname: Gandalf
  info:
    grad_time_ms: 3586.95
    load_time_ms: 2.758
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.0003906250058207661
      cur_lr: 4.999999873689376e-05
      entropy: 1.3623945713043213
      kl: 0.003060264978557825
      policy_loss: -0.0006501601310446858
      tota

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=26994], 6792 s, 280 iter, 2800000 ts, 339 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_20-18-48
  done: false
  episode_len_mean: 138.77
  episode_reward_max: 385.9884798918771
  episode_reward_mean: 339.49902299640866
  episode_reward_min: -141.9700022070712
  episodes_this_iter: 72
  episodes_total: 19528
  experiment_id: 3c083513fdcf4257a3e2216ed5864a2f
  hostname: Gandalf
  info:
    grad_time_ms: 3458.255
    load_time_ms: 2.366
    num_steps_sampled: 2810000
    num_steps_trained: 2810000
    rl_0:
      cur_kl_coeff: 1.0289713229853388e-18
      cur_lr: 4.999999873689376e-05
      entropy: 0.6252782344818115
      kl: 0.018818004056811333
      policy_loss: 0.0010682898573577404
   

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=26994], 6912 s, 285 iter, 2850000 ts, 339 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_20-20-48
  done: false
  episode_len_mean: 138.86
  episode_reward_max: 373.127547335813
  episode_reward_mean: 327.88344526922674
  episode_reward_min: -144.0894721050268
  episodes_this_iter: 72
  episodes_total: 19889
  experiment_id: 3c083513fdcf4257a3e2216ed5864a2f
  hostname: Gandalf
  info:
    grad_time_ms: 3448.285
    load_time_ms: 2.227
    num_steps_sampled: 2860000
    num_steps_trained: 2860000
    rl_0:
      cur_kl_coeff: 2.315185063126706e-18
      cur_lr: 4.999999873689376e-05
      entropy: 0.6161824464797974
      kl: 0.016290538012981415
      policy_loss: -0.0015007787151262164
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=26994], 7033 s, 290 iter, 2900000 ts, 341 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_20-22-49
  done: false
  episode_len_mean: 140.16
  episode_reward_max: 378.77503093862805
  episode_reward_mean: 339.0726618930933
  episode_reward_min: 19.960065262902333
  episodes_this_iter: 72
  episodes_total: 20247
  experiment_id: 3c083513fdcf4257a3e2216ed5864a2f
  hostname: Gandalf
  info:
    grad_time_ms: 3452.083
    load_time_ms: 2.311
    num_steps_sampled: 2910000
    num_steps_trained: 2910000
    rl_0:
      cur_kl_coeff: 2.315185063126706e-18
      cur_lr: 4.999999873689376e-05
      entropy: 0.6279006600379944
      kl: 0.0268265288323164
      policy_loss: 0.0007481768843717873
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=26994], 7154 s, 295 iter, 2950000 ts, 331 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_20-24-51
  done: false
  episode_len_mean: 140.36
  episode_reward_max: 375.1510592504099
  episode_reward_mean: 337.5222488564645
  episode_reward_min: 163.3328903890441
  episodes_this_iter: 72
  episodes_total: 20608
  experiment_id: 3c083513fdcf4257a3e2216ed5864a2f
  hostname: Gandalf
  info:
    grad_time_ms: 3457.743
    load_time_ms: 2.373
    num_steps_sampled: 2960000
    num_steps_trained: 2960000
    rl_0:
      cur_kl_coeff: 7.813751552606587e-18
      cur_lr: 4.999999873689376e-05
      entropy: 0.6391147375106812
      kl: 61.53817367553711
      policy_loss: 0.10306043922901154
      total

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=26994], 7275 s, 300 iter, 3000000 ts, 342 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=26994], 7275 s, 300 iter, 3000000 ts, 342 rew



In [13]:
executeTraining()

 Starting SUMO on port 41009
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.7/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-12_20-26-29hvez1r1v -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



11.81848450957205
2.4475537966176044


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_20-27-29
  done: false
  episode_len_mean: 461.76190476190476
  episode_reward_max: 169.89625099605405
  episode_reward_mean: 13.840764374215118
  episode_reward_min: -153.2152350975988
  episodes_this_iter: 21
  episodes_total: 21
  experiment_id: 9d4e53469e9e4300bdec46d00feb8803
  hostname: Gandalf
  info:
    grad_time_ms: 4553.048
    load_time_ms: 144.467
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4170629978179932
      kl: 0.001030373852699995
      policy_loss: -0.0011537749087437987
      total_loss: 128.91114807128906
      vf_explained_var: 0.014319413341581821
      vf_loss: 128.91207885742188
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.418864369392395
      kl: 0.0012330821482464671
      policy_loss: -0.0009915238

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28815], 121 s, 5 iter, 50000 ts, 64.7 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_20-29-28
  done: false
  episode_len_mean: 454.39
  episode_reward_max: 300.00309345178084
  episode_reward_mean: 87.37004122309301
  episode_reward_min: -153.96501866118967
  episodes_this_iter: 22
  episodes_total: 130
  experiment_id: 9d4e53469e9e4300bdec46d00feb8803
  hostname: Gandalf
  info:
    grad_time_ms: 3697.481
    load_time_ms: 26.016
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4201107025146484
      kl: 0.003641005139797926
      policy_loss: -0.001972984755411744
      total_

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28815], 241 s, 10 iter, 100000 ts, 174 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_20-31-28
  done: false
  episode_len_mean: 279.28
  episode_reward_max: 346.6498795018241
  episode_reward_mean: 172.42275693171666
  episode_reward_min: -165.1169443983627
  episodes_this_iter: 37
  episodes_total: 289
  experiment_id: 9d4e53469e9e4300bdec46d00feb8803
  hostname: Gandalf
  info:
    grad_time_ms: 3525.054
    load_time_ms: 2.514
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.0003906250058207661
      cur_lr: 4.999999873689376e-05
      entropy: 1.3900965452194214
      kl: 0.010811024345457554
      policy_loss: -0.0030879033729434013
      tota

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28815], 6718 s, 280 iter, 2800000 ts, 337 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_22-19-38
  done: false
  episode_len_mean: 123.89
  episode_reward_max: 387.458014170307
  episode_reward_mean: 329.3818440343797
  episode_reward_min: -146.8843706377666
  episodes_this_iter: 80
  episodes_total: 20482
  experiment_id: 9d4e53469e9e4300bdec46d00feb8803
  hostname: Gandalf
  info:
    grad_time_ms: 3358.057
    load_time_ms: 2.43
    num_steps_sampled: 2810000
    num_steps_trained: 2810000
    rl_0:
      cur_kl_coeff: 1.226136156284215e-42
      cur_lr: 4.999999873689376e-05
      entropy: 0.6299318075180054
      kl: 0.015244579873979092
      policy_loss: 0.0029278965666890144
      t

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28815], 6837 s, 285 iter, 2850000 ts, 343 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_22-21-38
  done: false
  episode_len_mean: 125.46
  episode_reward_max: 387.78641606658084
  episode_reward_mean: 344.6654184729412
  episode_reward_min: -141.6596187034028
  episodes_this_iter: 79
  episodes_total: 20881
  experiment_id: 9d4e53469e9e4300bdec46d00feb8803
  hostname: Gandalf
  info:
    grad_time_ms: 3360.72
    load_time_ms: 2.408
    num_steps_sampled: 2860000
    num_steps_trained: 2860000
    rl_0:
      cur_kl_coeff: 1.83850358519416e-42
      cur_lr: 4.999999873689376e-05
      entropy: 0.6410022377967834
      kl: 0.010110048577189445
      policy_loss: 0.002494267886504531
      t

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28815], 6957 s, 290 iter, 2900000 ts, 351 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_22-23-38
  done: false
  episode_len_mean: 125.1
  episode_reward_max: 388.44506232638366
  episode_reward_mean: 347.3813167435468
  episode_reward_min: -134.39383357585027
  episodes_this_iter: 81
  episodes_total: 21282
  experiment_id: 9d4e53469e9e4300bdec46d00feb8803
  hostname: Gandalf
  info:
    grad_time_ms: 3347.528
    load_time_ms: 2.479
    num_steps_sampled: 2910000
    num_steps_trained: 2910000
    rl_0:
      cur_kl_coeff: 9.1925179259708e-43
      cur_lr: 4.999999873689376e-05
      entropy: 0.6347320079803467
      kl: 0.03716764599084854
      policy_loss: 0.00031013289117254317
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28815], 7077 s, 295 iter, 2950000 ts, 341 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_22-25-38
  done: false
  episode_len_mean: 125.82
  episode_reward_max: 389.3992650926119
  episode_reward_mean: 349.6721077764297
  episode_reward_min: -140.9449402879667
  episodes_this_iter: 79
  episodes_total: 21680
  experiment_id: 9d4e53469e9e4300bdec46d00feb8803
  hostname: Gandalf
  info:
    grad_time_ms: 3351.27
    load_time_ms: 2.492
    num_steps_sampled: 2960000
    num_steps_trained: 2960000
    rl_0:
      cur_kl_coeff: 1.37887768889562e-42
      cur_lr: 4.999999873689376e-05
      entropy: 0.7171923518180847
      kl: 0.008917853236198425
      policy_loss: -3.608163387980312e-05
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=28815], 7196 s, 300 iter, 3000000 ts, 337 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=28815], 7196 s, 300 iter, 3000000 ts, 337 rew



In [14]:
executeTraining()

 Starting SUMO on port 57437
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.1/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-12_22-27-15ke_66_iv -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



10.01081822073232
26.104054807852993


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_22-28-15
  done: false
  episode_len_mean: 434.3333333333333
  episode_reward_max: 193.38667648657946
  episode_reward_mean: 30.09197565530791
  episode_reward_min: -156.0618412190695
  episodes_this_iter: 21
  episodes_total: 21
  experiment_id: e3ae719ff1ee406e8a8b95dc8378f8e3
  hostname: Gandalf
  info:
    grad_time_ms: 4525.795
    load_time_ms: 140.201
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4199107885360718
      kl: 0.0014287193771451712
      policy_loss: -0.002639362821355462
      total_loss: 114.3130111694336
      vf_explained_var: 0.018698977306485176
      vf_loss: 114.31536865234375
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4217541217803955
      kl: 0.001456847763620317
      policy_loss: -0.0017349777044

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28878], 122 s, 5 iter, 50000 ts, 98.3 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_22-30-15
  done: false
  episode_len_mean: 410.99
  episode_reward_max: 357.71019220620303
  episode_reward_mean: 120.9981200309501
  episode_reward_min: -159.92121765714262
  episodes_this_iter: 29
  episodes_total: 141
  experiment_id: e3ae719ff1ee406e8a8b95dc8378f8e3
  hostname: Gandalf
  info:
    grad_time_ms: 3711.202
    load_time_ms: 25.29
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4009897708892822
      kl: 0.00981423445045948
      policy_loss: -0.003668017452582717
      total_lo

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28878], 241 s, 10 iter, 100000 ts, 199 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-12_22-32-15
  done: false
  episode_len_mean: 265.33
  episode_reward_max: 356.78928076891947
  episode_reward_mean: 209.11282151594085
  episode_reward_min: -162.9732527461369
  episodes_this_iter: 38
  episodes_total: 318
  experiment_id: e3ae719ff1ee406e8a8b95dc8378f8e3
  hostname: Gandalf
  info:
    grad_time_ms: 3552.636
    load_time_ms: 2.286
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.3909927606582642
      kl: 0.0024774454068392515
      policy_loss: -0.0010783475590869784
      t

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28878], 7262 s, 280 iter, 2800000 ts, 311 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_00-29-29
  done: false
  episode_len_mean: 148.81
  episode_reward_max: 380.8634916149974
  episode_reward_mean: 329.3819372833942
  episode_reward_min: -142.3108123095656
  episodes_this_iter: 67
  episodes_total: 18415
  experiment_id: e3ae719ff1ee406e8a8b95dc8378f8e3
  hostname: Gandalf
  info:
    grad_time_ms: 3361.368
    load_time_ms: 2.387
    num_steps_sampled: 2810000
    num_steps_trained: 2810000
    rl_0:
      cur_kl_coeff: 1.821688003622262e-43
      cur_lr: 4.999999873689376e-05
      entropy: 0.21782101690769196
      kl: 0.02030303329229355
      policy_loss: -0.002026123460382223
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28878], 7381 s, 285 iter, 2850000 ts, 303 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_00-31-28
  done: false
  episode_len_mean: 144.88
  episode_reward_max: 383.2025180796089
  episode_reward_mean: 308.29415726683106
  episode_reward_min: -145.61582635756113
  episodes_this_iter: 68
  episodes_total: 18757
  experiment_id: e3ae719ff1ee406e8a8b95dc8378f8e3
  hostname: Gandalf
  info:
    grad_time_ms: 3353.045
    load_time_ms: 2.371
    num_steps_sampled: 2860000
    num_steps_trained: 2860000
    rl_0:
      cur_kl_coeff: 9.10844001811131e-44
      cur_lr: 4.999999873689376e-05
      entropy: 0.1930840164422989
      kl: 0.015467746183276176
      policy_loss: 0.0011313441209495068
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28878], 7500 s, 290 iter, 2900000 ts, 322 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_00-33-28
  done: false
  episode_len_mean: 149.65
  episode_reward_max: 378.1354095237104
  episode_reward_mean: 339.1078264186592
  episode_reward_min: 295.2858835914802
  episodes_this_iter: 67
  episodes_total: 19097
  experiment_id: e3ae719ff1ee406e8a8b95dc8378f8e3
  hostname: Gandalf
  info:
    grad_time_ms: 3356.883
    load_time_ms: 2.266
    num_steps_sampled: 2910000
    num_steps_trained: 2910000
    rl_0:
      cur_kl_coeff: 9.10844001811131e-44
      cur_lr: 4.999999873689376e-05
      entropy: 0.09081870317459106
      kl: 0.024350423365831375
      policy_loss: -0.0022661809343844652
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=28878], 7619 s, 295 iter, 2950000 ts, 337 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_00-35-27
  done: false
  episode_len_mean: 148.44
  episode_reward_max: 387.0590326055178
  episode_reward_mean: 330.20938329202016
  episode_reward_min: -146.7462331781263
  episodes_this_iter: 68
  episodes_total: 19436
  experiment_id: e3ae719ff1ee406e8a8b95dc8378f8e3
  hostname: Gandalf
  info:
    grad_time_ms: 3356.634
    load_time_ms: 2.331
    num_steps_sampled: 2960000
    num_steps_trained: 2960000
    rl_0:
      cur_kl_coeff: 4.484155085839415e-44
      cur_lr: 4.999999873689376e-05
      entropy: 0.13722443580627441
      kl: 0.029280683025717735
      policy_loss: -0.0013283913722261786
  

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=28878], 7737 s, 300 iter, 3000000 ts, 321 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=28878], 7737 s, 300 iter, 3000000 ts, 321 rew



In [15]:
executeTraining()

 Starting SUMO on port 55707
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.4/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-13_00-37-03ula1uqx_ -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



23.724963860171645
26.27183767579561


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_00-37-42
  done: false
  episode_len_mean: 499.0
  episode_reward_max: 173.63690576553265
  episode_reward_mean: 90.72541522801056
  episode_reward_min: -113.69505547852305
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: deab26f2a5e54fe0ae1da2fc0714f80d
  hostname: Gandalf
  info:
    grad_time_ms: 4585.186
    load_time_ms: 151.821
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4192588329315186
      kl: 0.0019781726878136396
      policy_loss: -0.002234462648630142
      total_loss: 26.256221771240234
      vf_explained_var: 0.2183620035648346
      vf_loss: 26.258060455322266
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4185649156570435
      kl: 0.0010123230749741197
      policy_loss: -0.001407453790307045
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=30948], 118 s, 5 iter, 50000 ts, 110 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_00-39-39
  done: false
  episode_len_mean: 401.04
  episode_reward_max: 377.2050247439947
  episode_reward_mean: 139.96828155257873
  episode_reward_min: -164.2127675261156
  episodes_this_iter: 30
  episodes_total: 141
  experiment_id: deab26f2a5e54fe0ae1da2fc0714f80d
  hostname: Gandalf
  info:
    grad_time_ms: 3695.495
    load_time_ms: 27.361
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4230947494506836
      kl: 0.00855925865471363
      policy_loss: -0.0036022854037582874
      total_lo

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=30948], 237 s, 10 iter, 100000 ts, 157 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_00-41-38
  done: false
  episode_len_mean: 206.82
  episode_reward_max: 383.3729331036498
  episode_reward_mean: 151.57002810282427
  episode_reward_min: -160.878312516247
  episodes_this_iter: 52
  episodes_total: 352
  experiment_id: deab26f2a5e54fe0ae1da2fc0714f80d
  hostname: Gandalf
  info:
    grad_time_ms: 3521.379
    load_time_ms: 2.554
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.3818913698196411
      kl: 0.0037152159493416548
      policy_loss: -0.0005438837688416243
      tot

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=30948], 6739 s, 280 iter, 2800000 ts, 331 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_02-30-13
  done: false
  episode_len_mean: 135.64
  episode_reward_max: 389.52936021771296
  episode_reward_mean: 326.5245024742306
  episode_reward_min: -140.97606204255564
  episodes_this_iter: 73
  episodes_total: 19327
  experiment_id: deab26f2a5e54fe0ae1da2fc0714f80d
  hostname: Gandalf
  info:
    grad_time_ms: 3433.83
    load_time_ms: 2.502
    num_steps_sampled: 2810000
    num_steps_trained: 2810000
    rl_0:
      cur_kl_coeff: 2.2664148835513015e-25
      cur_lr: 4.999999873689376e-05
      entropy: -0.13349999487400055
      kl: 0.01630588062107563
      policy_loss: 0.000559977546799928
   

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=30948], 6858 s, 285 iter, 2850000 ts, 317 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_02-32-11
  done: false
  episode_len_mean: 135.05
  episode_reward_max: 391.397481235236
  episode_reward_mean: 315.4610864638973
  episode_reward_min: -140.22677436511563
  episodes_this_iter: 74
  episodes_total: 19698
  experiment_id: deab26f2a5e54fe0ae1da2fc0714f80d
  hostname: Gandalf
  info:
    grad_time_ms: 3433.439
    load_time_ms: 2.274
    num_steps_sampled: 2860000
    num_steps_trained: 2860000
    rl_0:
      cur_kl_coeff: 2.2664148835513015e-25
      cur_lr: 4.999999873689376e-05
      entropy: -0.06562212109565735
      kl: 0.020898666232824326
      policy_loss: 0.00047433949657715857
 

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=30948], 6977 s, 290 iter, 2900000 ts, 307 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_02-34-11
  done: false
  episode_len_mean: 134.22
  episode_reward_max: 392.0805302185082
  episode_reward_mean: 313.9766169283164
  episode_reward_min: -144.6326965702824
  episodes_this_iter: 73
  episodes_total: 20068
  experiment_id: deab26f2a5e54fe0ae1da2fc0714f80d
  hostname: Gandalf
  info:
    grad_time_ms: 3440.547
    load_time_ms: 2.24
    num_steps_sampled: 2910000
    num_steps_trained: 2910000
    rl_0:
      cur_kl_coeff: 5.099432070505989e-25
      cur_lr: 4.999999873689376e-05
      entropy: -0.0857827439904213
      kl: 0.015346994623541832
      policy_loss: 0.0004922738298773766
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=30948], 7097 s, 295 iter, 2950000 ts, 311 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_02-36-11
  done: false
  episode_len_mean: 135.14
  episode_reward_max: 385.6248790175055
  episode_reward_mean: 322.69625420970283
  episode_reward_min: -142.18210398450074
  episodes_this_iter: 73
  episodes_total: 20437
  experiment_id: deab26f2a5e54fe0ae1da2fc0714f80d
  hostname: Gandalf
  info:
    grad_time_ms: 3444.656
    load_time_ms: 2.304
    num_steps_sampled: 2960000
    num_steps_trained: 2960000
    rl_0:
      cur_kl_coeff: 1.1473720556264762e-24
      cur_lr: 4.999999873689376e-05
      entropy: -0.13401784002780914
      kl: 0.01770164631307125
      policy_loss: 0.002717869356274605
 

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=30948], 7216 s, 300 iter, 3000000 ts, 323 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=30948], 7216 s, 300 iter, 3000000 ts, 323 rew



In [16]:
executeTraining()

 Starting SUMO on port 42781
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-13_02-37-488i2grp5y -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



18.377068983595844
28.059751325730154


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_02-38-47
  done: false
  episode_len_mean: 500.0
  episode_reward_max: 235.037198121984
  episode_reward_mean: 121.41440899553632
  episode_reward_min: 43.69189411821678
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: de3c47973cd9444396776c50d009e997
  hostname: Gandalf
  info:
    grad_time_ms: 4623.289
    load_time_ms: 150.645
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4203523397445679
      kl: 0.0021946991328150034
      policy_loss: -0.003515524324029684
      total_loss: 15.115537643432617
      vf_explained_var: 0.30585241317749023
      vf_loss: 15.11861801147461
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4170756340026855
      kl: 0.0026930130552500486
      policy_loss: -0.003957070875912905
      to

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3789], 124 s, 5 iter, 50000 ts, 98.7 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_02-40-49
  done: false
  episode_len_mean: 407.51
  episode_reward_max: 376.4254978318797
  episode_reward_mean: 103.20165400945702
  episode_reward_min: -158.69016618129467
  episodes_this_iter: 26
  episodes_total: 139
  experiment_id: de3c47973cd9444396776c50d009e997
  hostname: Gandalf
  info:
    grad_time_ms: 3802.33
    load_time_ms: 27.298
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4116982221603394
      kl: 0.003458708059042692
      policy_loss: -0.002234934363514185
      total_l

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3789], 246 s, 10 iter, 100000 ts, 166 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_02-42-51
  done: false
  episode_len_mean: 247.8
  episode_reward_max: 381.2699348859451
  episode_reward_mean: 209.93973449875003
  episode_reward_min: -151.67586958049446
  episodes_this_iter: 43
  episodes_total: 320
  experiment_id: de3c47973cd9444396776c50d009e997
  hostname: Gandalf
  info:
    grad_time_ms: 3619.266
    load_time_ms: 2.624
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.4221855401992798
      kl: 0.003315133508294821
      policy_loss: -0.002263287315145135
      tota

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3789], 6740 s, 280 iter, 2800000 ts, 330 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_04-31-18
  done: false
  episode_len_mean: 125.74
  episode_reward_max: 366.04408579404793
  episode_reward_mean: 331.34151314524416
  episode_reward_min: 299.18559536989983
  episodes_this_iter: 79
  episodes_total: 20849
  experiment_id: de3c47973cd9444396776c50d009e997
  hostname: Gandalf
  info:
    grad_time_ms: 3457.8
    load_time_ms: 2.478
    num_steps_sampled: 2810000
    num_steps_trained: 2810000
    rl_0:
      cur_kl_coeff: 5.445537397100722e-25
      cur_lr: 4.999999873689376e-05
      entropy: 0.33681726455688477
      kl: 0.012011951766908169
      policy_loss: 0.0018463238375261426
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3789], 6860 s, 285 iter, 2850000 ts, 330 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_04-33-19
  done: false
  episode_len_mean: 126.87
  episode_reward_max: 371.3359735389686
  episode_reward_mean: 332.1260714844162
  episode_reward_min: 296.1194867628927
  episodes_this_iter: 79
  episodes_total: 21246
  experiment_id: de3c47973cd9444396776c50d009e997
  hostname: Gandalf
  info:
    grad_time_ms: 3465.388
    load_time_ms: 2.384
    num_steps_sampled: 2860000
    num_steps_trained: 2860000
    rl_0:
      cur_kl_coeff: 5.445537397100722e-25
      cur_lr: 4.999999873689376e-05
      entropy: 0.35673797130584717
      kl: 0.024102259427309036
      policy_loss: 0.009557120501995087
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.2/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3789], 6980 s, 290 iter, 2900000 ts, 336 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_04-35-19
  done: false
  episode_len_mean: 127.37
  episode_reward_max: 371.88325987485416
  episode_reward_mean: 337.4829661938252
  episode_reward_min: 302.99334657645835
  episodes_this_iter: 79
  episodes_total: 21640
  experiment_id: de3c47973cd9444396776c50d009e997
  hostname: Gandalf
  info:
    grad_time_ms: 3450.279
    load_time_ms: 2.246
    num_steps_sampled: 2910000
    num_steps_trained: 2910000
    rl_0:
      cur_kl_coeff: 8.1683065886891485e-25
      cur_lr: 4.999999873689376e-05
      entropy: 0.34254810214042664
      kl: 0.014994997531175613
      policy_loss: 0.005912939086556435
   

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3789], 7100 s, 295 iter, 2950000 ts, 336 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_04-37-18
  done: false
  episode_len_mean: 127.31
  episode_reward_max: 379.8059656112418
  episode_reward_mean: 339.81511294091865
  episode_reward_min: 291.78810216290236
  episodes_this_iter: 79
  episodes_total: 22033
  experiment_id: de3c47973cd9444396776c50d009e997
  hostname: Gandalf
  info:
    grad_time_ms: 3439.019
    load_time_ms: 2.456
    num_steps_sampled: 2960000
    num_steps_trained: 2960000
    rl_0:
      cur_kl_coeff: 1.2252459389995657e-24
      cur_lr: 4.999999873689376e-05
      entropy: 0.36555248498916626
      kl: 0.020335543900728226
      policy_loss: 0.007112202700227499
   

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=3789], 7219 s, 300 iter, 3000000 ts, 340 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=3789], 7219 s, 300 iter, 3000000 ts, 340 rew



In [17]:
executeTraining()

 Starting SUMO on port 57389
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.1/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-13_04-38-5556_jtq95 -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



8.428299975431056
25.44103369554646


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_04-39-56
  done: false
  episode_len_mean: 459.55
  episode_reward_max: 156.6480706130009
  episode_reward_mean: 54.223883915774216
  episode_reward_min: -163.98291414907604
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: 69ac22f84045446ca531c2e60e3bb351
  hostname: Gandalf
  info:
    grad_time_ms: 4548.829
    load_time_ms: 150.365
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4194523096084595
      kl: 0.0005114871310070157
      policy_loss: -0.0006777705857530236
      total_loss: 69.36656188964844
      vf_explained_var: 0.02261347882449627
      vf_loss: 69.36713409423828
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.420228362083435
      kl: 0.0003566278319340199
      policy_loss: -0.001174206379801035
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3852], 122 s, 5 iter, 50000 ts, 103 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_04-41-56
  done: false
  episode_len_mean: 439.06
  episode_reward_max: 326.95824978464543
  episode_reward_mean: 129.9293865269946
  episode_reward_min: -165.0442810664234
  episodes_this_iter: 27
  episodes_total: 134
  experiment_id: 69ac22f84045446ca531c2e60e3bb351
  hostname: Gandalf
  info:
    grad_time_ms: 3716.356
    load_time_ms: 27.212
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.40365731716156
      kl: 0.0033728349953889847
      policy_loss: -0.0021078006830066442
      total_lo

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3852], 243 s, 10 iter, 100000 ts, 150 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_04-43-57
  done: false
  episode_len_mean: 305.75
  episode_reward_max: 392.70472427486925
  episode_reward_mean: 178.0509180126735
  episode_reward_min: -156.4303541368106
  episodes_this_iter: 35
  episodes_total: 295
  experiment_id: 69ac22f84045446ca531c2e60e3bb351
  hostname: Gandalf
  info:
    grad_time_ms: 3550.227
    load_time_ms: 2.465
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.4182851314544678
      kl: 0.004295974969863892
      policy_loss: -0.0019421875476837158
      tot

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3852], 6768 s, 280 iter, 2800000 ts, 315 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_06-32-55
  done: false
  episode_len_mean: 125.95
  episode_reward_max: 367.5496675198047
  episode_reward_mean: 320.92874817071805
  episode_reward_min: 281.27392909041913
  episodes_this_iter: 78
  episodes_total: 21176
  experiment_id: 69ac22f84045446ca531c2e60e3bb351
  hostname: Gandalf
  info:
    grad_time_ms: 3421.79
    load_time_ms: 2.544
    num_steps_sampled: 2810000
    num_steps_trained: 2810000
    rl_0:
      cur_kl_coeff: 6.075970618562437e-14
      cur_lr: 4.999999873689376e-05
      entropy: 0.8460533022880554
      kl: 32.81127166748047
      policy_loss: 0.06402231007814407
      tota

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3852], 6889 s, 285 iter, 2850000 ts, 322 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_06-34-56
  done: false
  episode_len_mean: 126.25
  episode_reward_max: 372.49596035847446
  episode_reward_mean: 311.923776218956
  episode_reward_min: -140.35273580806327
  episodes_this_iter: 79
  episodes_total: 21572
  experiment_id: 69ac22f84045446ca531c2e60e3bb351
  hostname: Gandalf
  info:
    grad_time_ms: 3416.312
    load_time_ms: 2.416
    num_steps_sampled: 2860000
    num_steps_trained: 2860000
    rl_0:
      cur_kl_coeff: 2.0506402023494352e-13
      cur_lr: 4.999999873689376e-05
      entropy: 0.8817878365516663
      kl: 30.256187438964844
      policy_loss: 0.045571185648441315
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3852], 7010 s, 290 iter, 2900000 ts, 320 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_06-36-58
  done: false
  episode_len_mean: 127.32
  episode_reward_max: 372.5288542774193
  episode_reward_mean: 324.030401276091
  episode_reward_min: 286.4712460997036
  episodes_this_iter: 79
  episodes_total: 21968
  experiment_id: 69ac22f84045446ca531c2e60e3bb351
  hostname: Gandalf
  info:
    grad_time_ms: 3402.47
    load_time_ms: 2.241
    num_steps_sampled: 2910000
    num_steps_trained: 2910000
    rl_0:
      cur_kl_coeff: 2.306971074676062e-13
      cur_lr: 4.999999873689376e-05
      entropy: 0.8988209962844849
      kl: 0.014435973018407822
      policy_loss: 0.0023898521903902292
      to

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=3852], 7131 s, 295 iter, 2950000 ts, 321 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-13_06-38-59
  done: false
  episode_len_mean: 126.17
  episode_reward_max: 377.42600858272016
  episode_reward_mean: 319.2806483676348
  episode_reward_min: 159.3449023834841
  episodes_this_iter: 79
  episodes_total: 22364
  experiment_id: 69ac22f84045446ca531c2e60e3bb351
  hostname: Gandalf
  info:
    grad_time_ms: 3415.306
    load_time_ms: 2.268
    num_steps_sampled: 2960000
    num_steps_trained: 2960000
    rl_0:
      cur_kl_coeff: 2.306971074676062e-13
      cur_lr: 4.999999873689376e-05
      entropy: 0.8429166078567505
      kl: 0.009739730507135391
      policy_loss: 0.00043980739428661764
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=3852], 7252 s, 300 iter, 3000000 ts, 315 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 11.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=3852], 7252 s, 300 iter, 3000000 ts, 315 rew

